In [1]:
import os
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import plotly.graph_objects as go

In [3]:
df = pd.read_excel('/Volumes/Seagate Expansi/PhD Files/Data/AlbatrossOneData/06_2020/V3_F3.xlsx',sheet_name = 'DFDR_F3',
                  header=None)

In [4]:
df = df.fillna(method='ffill', axis=1)
df.head(5)

0                1             2                 3   \
0                Time             Time          Time              Time   
1  Master SW time (s)     VTP CAM time  VTP CAM time  Aircraft T/O (s)   
2              126.07  00:00:54.570000         54.57                 0   
3              126.09  00:00:54.590000         54.57                 0   
4              126.11  00:00:54.610000         54.59                 0   

         4         5         6         7         8         9   ...  \
0  SG Zerod  SG Zerod  SG Zerod  SG Zerod  SG Zerod  SG Zerod  ...   
1       SG1       SG2       SG3       SG4       SG5       SG6  ...   
2        17       122        34        18         2         2  ...   
3        26       134        48        23        -2         5  ...   
4        25       134        47        23       -17        -1  ...   

              82                83              84              85  \
0      RPMr(rpm)           Celr(V)       ASpd(mph)       ASpd(m/s)   
1  Right fan RPM  Left battery (V)  Airspeed (mph)  Airspeed (m/s)   
2              1                 1               1               1   
3        1.02022           1.02022         1.02022         1.02022   
4        1.02813           1.02813         1.02813         1.02813   

                  86                     87                     88  \
0            Cell(V)              eng1(mAh)              eng2(mAh)   
1  Right battery (V)  Engine 1 mAh consumed  Engine 2 mAh consumed   
2                  1                      1                      1   
3            1.02022                1.02022                1.02022   
4            1.02813                1.02813                1.02813   

                              89  \
0                            Thr   
1  Flaps full / take-off / clean   
2                              1   
3                        1.02022   
4                        1.02813   

                                                 90       91  
0                                                6P       SH  
1  Tips Grd / H/L / H/L / Cruise / Cruise / Release   Brakes  
2                                                 1        1  
3                                           1.02022  1.02022  
4                                           1.02813  1.02813  

[5 rows x 92 columns]

In [5]:
#plt.plot(df[0][2:]-df[0][2],df[55][2:])
plt.plot(df[0][2:]-df[0][2],df[57][2:])

In [37]:
def get_angle_data(filename,flip=False):
    df2 = pd.read_csv(filename)
    df2['t'] = df2['Frame']/df2['fps']
    df2['x_delta'] = df2['x0'] - df2['x1']
    df2['y_delta'] = df2['y0'] - df2['y1']
    df2['x_delta'] = df2['x_delta'].where((df2['x0']>df2['x1']).to_list(),df2['x1']-df2['x0'])
    df2['y_delta'] = df2['y_delta'].where((df2['x0']>df2['x1']).to_list(),df2['y1']-df2['y0'])
    df2['angle'] = np.rad2deg(np.arctan2(df2['y_delta'],df2['x_delta']))
    df2['angle'] = df2['angle'] if not flip else -df2['angle']
    return df2

In [38]:
df_left = get_angle_data('/Volumes/Seagate Expansi/PhD Files/Data/AlbatrossOneData/06_2020/FLT2_3_data_left.csv',False)
df_right = get_angle_data('/Volumes/Seagate Expansi/PhD Files/Data/AlbatrossOneData/06_2020/FLT2_3_data_right.csv',True) 

In [39]:
calib = get_angle_data('/Volumes/Seagate Expansi/PhD Files/Data/AlbatrossOneData/06_2020/calibpoints.csv')
calib['angle'] = calib['angle'].where(calib['wingtip']=='left',-calib['angle'])
flight = 3

left_x_c = calib[(calib['flight']==flight)&(calib['wingtip']=='left')]['angle']
left_y_c = calib[(calib['flight']==flight)&(calib['wingtip']=='left')]['angle_act']

right_x_c = calib[(calib['flight']==flight)&(calib['wingtip']=='right')]['angle']
right_y_c = calib[(calib['flight']==flight)&(calib['wingtip']=='right')]['angle_act']

df_left['angle_calib'] = np.interp(df_left['angle'],left_x_c,left_y_c)
df_right['angle_calib'] = np.interp(df_right['angle'],right_x_c,right_y_c)                                     

In [40]:
plt.plot(df_right['t'],df_right['angle'])

In [49]:
# inital vlue for run 2 should be 22 degrees
inital_angle = {2:[22,22],3:[22,22],4:[22,22],4.1:[33.4,27.1]}

df_left['angle_calib'] = df_left['angle_calib'] + (inital_angle[flight][0]-np.mean(df_left['angle_calib'][1:200]))
df_right['angle_calib'] = df_right['angle_calib'] + (inital_angle[flight][1]-np.mean(df_right['angle_calib'][1:200]))
    

In [42]:

delta = 451.99-68.03
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_left['t']+delta, y=df_left['angle_calib'],
                    mode='lines',
                    name='left'))
fig.add_trace(go.Scatter(x=df_left['t']+delta, y=df_right['angle_calib'],
                    mode='lines',
                    name='right'))
# fig.add_trace(go.Scatter(x=df_right['t']+delta, y=-df_right['angle']+df_left['angle'],
#                     mode='lines',
#                     name='delta'))
fig.add_trace(go.Scatter(x=df[0][2:]-df[0][2], y=df[57][2:],
                    mode='lines',
                    name='roll'))
fig.add_trace(go.Scatter(x=df[0][2:]-df[0][2], y=df[55][2:]*25,
                    mode='lines',
                    name='status'))

fig.show()

In [43]:
df[92]=0
df[92][0]="FWT Angle"
df[92][1]="Left"
df[92][2:]=np.interp(df[0][2:]-df[0][2],df_left['t']+delta,df_left['angle_calib'])

df[93]=0
df[93][0]="FWT Angle"
df[93][1]="Right"
df[93][2:]=np.interp(df[0][2:]-df[0][2],df_right['t']+delta,df_right['angle_calib'])

/Users/fintan/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/Users/fintan/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:671: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/Users/fintan/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [44]:
df.head()

0                1             2                 3   \
0                Time             Time          Time              Time   
1  Master SW time (s)     VTP CAM time  VTP CAM time  Aircraft T/O (s)   
2              126.07  00:00:54.570000         54.57                 0   
3              126.09  00:00:54.590000         54.57                 0   
4              126.11  00:00:54.610000         54.59                 0   

         4         5         6         7         8         9   ...  \
0  SG Zerod  SG Zerod  SG Zerod  SG Zerod  SG Zerod  SG Zerod  ...   
1       SG1       SG2       SG3       SG4       SG5       SG6  ...   
2        17       122        34        18         2         2  ...   
3        26       134        48        23        -2         5  ...   
4        25       134        47        23       -17        -1  ...   

               84              85                 86                     87  \
0       ASpd(mph)       ASpd(m/s)            Cell(V)              eng1(mAh)   
1  Airspeed (mph)  Airspeed (m/s)  Right battery (V)  Engine 1 mAh consumed   
2               1               1                  1                      1   
3         1.02022         1.02022            1.02022                1.02022   
4         1.02813         1.02813            1.02813                1.02813   

                      88                             89  \
0              eng2(mAh)                            Thr   
1  Engine 2 mAh consumed  Flaps full / take-off / clean   
2                      1                              1   
3                1.02022                        1.02022   
4                1.02813                        1.02813   

                                                 90       91         92  \
0                                                6P       SH  FWT Angle   
1  Tips Grd / H/L / H/L / Cruise / Cruise / Release   Brakes       Left   
2                                                 1        1     22.087   
3                                           1.02022  1.02022     22.087   
4                                           1.02813  1.02813     22.087   

          93  
0  FWT Angle  
1      Right  
2    21.1014  
3    21.1014  
4    21.1014  

[5 rows x 94 columns]

In [46]:
df[[92,93]].to_clipboard(sep=',', index=False)

In [ ]:
df.to